# HW2

## Data
In this HW, I've used 2 data files, named data.json and game_name.json. Format of these files are json-line. These data were gathered by writing two spiders using scrapy. 

- data.json (and data_sample.json)

This file is crawled using Gamfa spider. Gamefa (Gamefa.com) is a perisan game news website, that covers all the news in video games industry. The spider starts with the home page, and iterates to next pages. There are almost 20 news in each page. Then the crawler opens all of these news pages, and extracts a json with form:
```
{
  'title': 'Title of the news',
  'time': 'Time of the news',
  'content': 'Body of the news, which is the main and longest text'
}
```
data.json consists of all data in this website, and it's ~ 300MB in size. Another file named data_sample.json is uploaded with this notebook, and it's a sample of the main file (~4MB). 

- game_name.json

This file is crawled using wikipedia spider. It starts from url https://en.wikipedia.org/wiki/Category:Video_games_by_year , and then crawls to pages related to games released in different years. Other pages were excluded. Using this logic, game_name.json is created which is a file with the name of all the games released after 1974.




## Initialization

First we install required packages.

In [ ]:
%pip install stanza spacy_stanza gputil hazm dadmatools

Then we initialize stanza persian pipline.

In [2]:
import stanza
import spacy_stanza
stanza.install_corenlp()
stanza.download("fa")

2022-04-20 18:32:31 WARNING: Directory /root/stanza_corenlp already exists. Please install CoreNLP to a new directory.


2022-04-20 18:32:32 INFO: Downloading default packages for language: fa (Persian)...
2022-04-20 18:32:34 INFO: File exists: /root/stanza_resources/fa/default.zip.
2022-04-20 18:32:38 INFO: Finished downloading models and saved to /root/stanza_resources.


I tried dadmatools package too, but the results wre better with stanza.

In [3]:
stanza_nlp = spacy_stanza.load_pipeline("fa")
# import dadmatools.pipeline.language as language
# pips = 'tok' 
# dadma_nlp = language.Pipeline(pips)

2022-04-20 18:32:38 INFO: Loading these models for language: fa (Persian):
| Processor | Package |
-----------------------
| tokenize  | perdt   |
| mwt       | perdt   |
| pos       | perdt   |
| lemma     | perdt   |
| depparse  | perdt   |

2022-04-20 18:32:38 INFO: Use device: cpu
2022-04-20 18:32:38 INFO: Loading: tokenize
2022-04-20 18:32:38 INFO: Loading: mwt
2022-04-20 18:32:38 INFO: Loading: pos
2022-04-20 18:32:38 INFO: Loading: lemma
2022-04-20 18:32:38 INFO: Loading: depparse
2022-04-20 18:32:39 INFO: Done loading processors!


## Reading Data

In this cell, data is read into data variable, and all games names are read into games variable.

In [4]:
import json

data = []
with open('data_sample.json') as f:
    for line in f:
        data.append(json.loads(line))

games = []
with open('game_name.json') as f:
    for line in f:
        games.append(json.loads(line)['name'])
games[:5]

['Cathode-ray tube amusement device',
 '2002 FIFA World Cup (video game)',
 'Ace Lightning',
 'Activision Anthology',
 'AdventureQuest']

This line prints the number of all documents. Note that this code is running on sample data.

In [5]:
print('Number of documents: ', len(data))

Number of documents:  959


## Preprocessing

I wanted to find keywords, and after seeing results, some terms had different writings so I handled these different writings here.

In [6]:
keywords = [
            (['ایکس باکس', 'ایکس‌باکس', 'xbox', 'Xbox', 'XBox'], 'ایکس-باکس'),
            (['پلی استیشن', 'پلی‌استیشن', 'play station', 'playstation', 'play-station'], 'پلی-استیشن'),
            (['نینتندو‌ سوئیچ', 'نینتندو سوییچ', 'Nintendo Switch', 'nintendo switch', 'Nintendo switch'], 'نینتندو-سوئیچ'),
]

In [7]:
import tqdm
for page in tqdm.tqdm(data):
    for keyword in keywords:
        for writing in keyword[0]:
          page['content'] = page['content'].replace(writing, keyword[1])


100%|██████████| 959/959 [00:00<00:00, 23368.97it/s]


In this section normalizers are defined.

In [8]:
from dadmatools.models.normalizer import Normalizer as N1
import hazm

normalizer1 = N1(
    full_cleaning=False,
    unify_chars=True,
    refine_punc_spacing=True,
    remove_extra_space=True,
    remove_puncs=False,
    remove_html=False,
    remove_stop_word=False,
    replace_email_with="<EMAIL>",
    replace_number_with=None,
    replace_url_with="<URL>",
    replace_mobile_number_with="<MOBILE_NUMBER>",
    replace_emoji_with="<EMOJI>",
    replace_home_number_with="<HOME_NUMBER>",
)
normalizer2 = hazm.Normalizer()

def normalize(text):
    text = normalizer2.normalize(normalizer1.normalize(text))
    return text


To be able to search for game names, I normalized game names too. Some characters like '(' had meaning in regex, so I put a '\\' before them.

In [9]:
games_normalized = []
for game in games:
  games_normalized.append(normalizer2.normalize(normalizer1.normalize(game)))
games_normalized = list(map(lambda x: x.replace('(','\(').replace(')', '\)').replace('.','\.'), games_normalized))
games_normalized[:10]


['Cathode-ray tube amusement device',
 '۲۰۰۲ FIFA World Cup \\(video game\\)',
 'Ace Lightning',
 'Activision Anthology',
 'AdventureQuest',
 'Aero Elite: Combat Academy',
 'Agassi Tennis Generation',
 'Age of Mythology',
 "Age of Wonders II: The Wizard's Throne",
 'Aggressive Inline \\(video game\\)']

Here I normalize the text, sentence tokenize the sentences and count the number of sentences.

In [10]:
sentences_count = 0
 
for page in tqdm.tqdm(data):
    page['content_normalized'] = normalize(page['content'])
    page['sentences'] = hazm.sent_tokenize(page['content_normalized'])
    sentences_count += len(page['sentences'])

print('\nNumber of sentences: ', sentences_count)

data[0]

100%|██████████| 959/959 [00:07<00:00, 131.69it/s]


Number of sentences:  20475


{'content': 'بن افلک و مت دیمون قرار است بار دیگر در فیلمی در مورد مدیر سابق کمپانی نایکی با یکدیگر همکاری کنند. بن افلک (Ben Affleck) و مت دیمون (Matt Damon) همکاری\u200cهای بسیار خوبی با یکدیگر داشته\u200cاند. حالا، آن\u200cها قرار است یک همکاری دیگر داشته باشند. آن\u200cها قرار است فیلمی بیوگرافی در مورد زندگی واقعی مدیر سابق کمپانی نایکی به نام سانی واکارو (Sonny Vaccarro) بسازند. ساخت این فیلم را کمپانی اسکای\u200cدنس اسپورتس و استودیو آمازون برعهده دارند. بن افلک علاوه بر نوشتن فیلم\u200cنامه این فیلم و نقش\u200cآفرینی در آن، قرار است کارگردانی فیلم را در دست داشته باشد. مت دیمون نیز علاوه بر همکاری در زمینه نوشتن فیلم\u200cنامه، قرار است در این فیلم بازی کند. این دو از جمله تهیه\u200cکنندگان فیلم خواهند بود. در این فیلم،\u200c مت دیمون نقش سانی واکارو را بازی خواهد کرد و بن افلک نیز نقش یکی از موسسان کمپانی نایکی به نام فیل نایت (Phil Knight) را به تصویر خواهد کشید. داستانی این فیلم در دهه هشتاد میلادی رخ می\u200cدهد و تلاش این کمپانی را به تصویر خواهد کشید که سعی داشتند تا بازی

## Tokenize and Merge neccessary tokens

The retokenizer is an important part of my code. Game names are not treated as a single entity (token). For example, 'Assasins Creed' is tokenized as 'Assasins' and 'Creed'. In this cell, we use a regex to find all game names, and then retokenize the tokens to make tokens like 'Assasins Creed' and not two seperate tokens. We call these tokens GAME Named Entities.

In [11]:
import re

games_expression = "|".join(games_normalized) 
def retokenize(text, doc):
    game_spans = list(
        map(
            lambda match: doc.char_span(*match.span(), label='GAME'),
            re.finditer(games_expression, doc.text),
        )
    )
    game_spans = list(filter(lambda span: span is not None, game_spans))
    doc.set_ents(game_spans)
    if game_spans:
      with doc.retokenize() as retokenizer:
          for span in game_spans:
              retokenizer.merge(span)


#### Method 1
In this method I iterated on all documents, and used stanze to tokenize. But this method was very slow. So don't run this code.

In [12]:
# # This doesn't work well, because doc takes a lot

# from nltk import FreqDist
# import timeit

# for page in tqdm.tqdm(data):
#     doc = stanza_nlp(page['content_normalized'])
#     retokenize(page['content_normalized'], doc)
#     page['tokens'] = map(lambda token: token.text, list(doc))

#### Method 2
This method wanted to solve problem of method 1, by concating all strings and then passing the string to stanza nlp pipline. But this method didn't work because stanza couldn't handle big strings. So don't run this code.

In [13]:
# # This doesn't work well, because string is too big
# from nltk import FreqDist
# import timeit

# contents = ''
# contents_list = list(map(lambda x: x['content'], data))
# for i, page in enumerate(tqdm.tqdm(data)):
#     contents += page['content'] + '\n\n'

# doc = stanza_nlp(contents)
# retokenize(contents, doc)
# words = list(doc)

#### Method 3
This is the main method that I used. I used the idea of method 2, to use batches and then process the batch all at once. This increases my speed and stanza could process the text also. 


In [14]:
from nltk import FreqDist
import timeit

batch_size = 200
contents_list = list(map(lambda x: x['content_normalized'], data))
page_count = len(contents_list)
i = 0
words = []
while i < page_count:
    print('i is', i)
    batch = contents_list[i:i+batch_size]
    i += batch_size

    contents = '\n\n'.join(batch)
    doc = stanza_nlp(contents)
    retokenize(contents, doc)
    words.extend(list(map(lambda token: token.text, list(doc))))

words_flat = words
words_flat[:10]

i is 0


/usr/local/lib/python3.7/dist-packages/stanza/models/common/beam.py:86: UserWarning: __floordiv__ is deprecated, and its behavior will change in a future version of pytorch. It currently rounds toward 0 (like the 'trunc' function NOT 'floor'). This results in incorrect rounding for negative values. To keep the current behavior, use torch.div(a, b, rounding_mode='trunc'), or for actual floor division, use torch.div(a, b, rounding_mode='floor').
  prevK = bestScoresId // numWords
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:15: UserWarning: Due to multiword token expansion or an alignment issue, the original text has been replaced by space-separated expanded tokens.
  from ipykernel import kernelapp as app
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:15: UserWarning: Can't set named entities because of multi-word token expansion or because the character offsets don't map to valid tokens produced by the Stanza tokenizer:
Words: ['بن', 'افلک', 'و', 'مت', 'دی

i is 200
i is 400


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:15: UserWarning: Can't set named entities because of multi-word token expansion or because the character offsets don't map to valid tokens produced by the Stanza tokenizer:
Words: ['بازی', 'Life', 'is', 'Strange', ':', 'Before', 'the', 'Storm', 'شرح', 'حال', 'کودک', 'یتیمی', 'است', 'که', 'با', 'از', 'دست', 'دادن', 'بابا', 'به', 'استقبال', 'بزرگسالی', 'می\u200cرود', '.', 'در', 'این', 'باره', 'چه', 'می\u200cتوان', 'گفت', '؟', 'شب\u200cهای', 'تنهایی', 'برای', 'دختری', 'شانزده', 'ساله', 'پر', 'شده\u200c', 'بودند', 'از', 'چیزهایی', 'که', 'توان', 'صحبت', 'را', 'از', 'او', 'می\u200cگرفتند', 'و', 'دردهایی', 'در', 'قلب', 'تازه', 'به', 'دوران', 'رسیده\u200c', 'اش', 'که', 'به', 'هیچ', 'زبانی', 'ترجمه', 'شدنی', 'نیستند', '.', 'تاریکی', 'شب', 'را', 'و', 'غصه\u200cهای', 'نوجوانی', 'را', 'و', 'سیاهی', 'از', 'دست', 'دادن', 'پاره', 'وجود', 'ت', 'را', 'کنار', 'هم', 'بگذار', 'و', 'این', 'داستان', 'از', 'بچه\u200c', 'یتیم\u200cهایی', 'که', 'دیگر

i is 600


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:15: UserWarning: Can't set named entities because of multi-word token expansion or because the character offsets don't map to valid tokens produced by the Stanza tokenizer:
Words: ['کشور', 'ژاپن', 'از', 'کارگردان', 'بازی\u200cهای', 'Metal', 'Gear', 'Solid', 'و', 'Death', 'Stranding', '،', 'هیدئو', 'کوجیما', '،', 'برای', 'تلاش\u200cهای', 'ش', 'در', 'عرصه', 'هنر', 'تقدیر', 'و', 'تشکر', 'کرد', '.', 'به\u200cتازگی', '،', 'هیدئو', 'کوجیما', '(', 'Hideo', 'Kojima', ')', 'برای', 'دستاوردهای', 'ارزنده\u200c', 'اش', 'در', 'عرصه\u200cهای', 'هنری', 'از', 'طرف', 'وزارت', 'فرهنگ', 'ژاپن', 'جایزه', 'گرفت', '.', 'از', 'سال', '۱۹۵۰', 'میلادی', 'تاکنون', '،', 'ژاپن', 'از', 'افرادی', 'که', 'در', 'زمینه\u200cهای', 'مختلف', 'هنری', 'دستاوردهای', 'قابل', 'توجهی', 'داشته', 'یا', 'تحول', 'مهمی', 'در', 'حوزه', 'فعالیت\u200c', 'خود', 'ایجاد', 'کرده', 'باشند', '،', 'با', 'جایزه', 'افتخاری', 'دستاورد', 'هنری', 'تقدیر', 'می\u200cکند', '.', 'کوجیما', 'ای

i is 800


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:15: UserWarning: Can't set named entities because of multi-word token expansion or because the character offsets don't map to valid tokens produced by the Stanza tokenizer:
Words: ['مایکروسافت', 'اعلام', 'کرده', 'است', 'که', 'فروش', 'محصولات', 'و', 'خدمات', 'خود', 'را', 'در', 'روسیه', 'متوقف', 'خواهد', 'کرد', '.', 'در', 'بیانیه', 'جدید', 'برد', 'اسمیت', '(', '\u200cBrad', 'Smith', ')', '،', 'رئیس', 'و', 'نایب', 'رئیس', 'مایکروسافت', '،', 'اعلام', 'شد', 'که', 'مایکروسافت', 'تا', 'زمانی', 'که', 'روسیه', 'به', 'حمله', 'به', 'اوکراین', 'ادامه', 'می\u200cدهد', '،', 'دیگر', 'در', 'این', 'کشور', 'تجارت', 'نخواهد', 'کرد', '.', 'اسمیت', 'گفت', ':', 'مانند', 'سایر', 'نقاط', 'جهان', '،', 'ما', 'از', 'تصاویر', 'و', 'اخباری', 'که', 'از', 'جنگ', 'در', 'اوکراین', 'می\u200cآید', 'وحشت', 'زده', '،', 'خشمگین', 'و', 'غمگین', 'هستیم', 'و', 'این', 'تهاجم', 'غیرقانونی', '،', 'غیرقابل', 'توجیه', 'و', 'ناعادلانه', 'روسیه', 'را', 'محکوم', 'می\u200cکن

['بن', 'افلک', 'و', 'مت', 'دیمون', 'قرار', 'است', 'بار', 'دیگر', 'در']


- Side Note: If we wanted to count only keywords frequncy, we didn't needed any of the above methods, and we could simply run this cell to tokenize texts. Note that in this method we couldn't retokenize and count games frequency

In [15]:
# from itertools import chain
# words = [[hazm.word_tokenize(sentence) for sentence in page['sentences']] for page in data]
# words_flat = list(chain(*list(chain(*words))))
# print(words_flat[:5])

Now we count the number of words, and get the most common words.

In [16]:
from nltk import FreqDist
import pandas as pd

common_words = FreqDist(words_flat).most_common(50)
pd.DataFrame(common_words)

0      1
0          .  19551
1          ،  17762
2          و  16293
3         در  16170
4         به  14330
5        این  12157
6         از  11788
7         که  11091
8         را   9085
9        است   8734
10        با   6223
11      بازی   5742
12         (   4427
13         )   4426
14      فیلم   4110
15      برای   4089
16        یک   3783
17        آن   3135
18       خود   2975
19       شده   2587
20         »   2492
21         «   2491
22        تا   2308
23         :   2183
24       نیز   2040
25       بود   2010
26        شد   1810
27      دارد   1710
28       اما   1684
29       کرد   1634
30        او   1618
31       سال   1608
32      قرار   1598
33        بر   1553
34    می‌شود   1510
35     خواهد   1506
36     سریال   1505
37    می‌کند   1360
38      کرده   1333
39       حال   1329
40       شما   1231
41     عنوان   1205
42     آن‌ها   1200
43      جدید   1188
44  بازی‌های   1111
45       روی   1102
46        هم   1026
47      وجود   1025
48     بسیار   1003
49     منتشر    977

As you can see, most common words are punctuations and stopwords.

In [17]:
import numpy as np
print('Number of words (including punctutaions and stopword): ', len(words_flat))
print ('Number of unique words: ', len(set(words_flat)))
average = np.sum([len(word) for word in words_flat])/len(words_flat)
print ('Average word length', average)
print ('Longest word', words_flat[np.argmax([len(word) for word in words_flat])])

Number of words (including punctutaions and stopword):  531775
Number of unique words:  28488
Average word length 3.863398993935405
Longest word Monster Hunter Stories ۲: Wings of Ruin


So we import stopwords ...

In [18]:
with open('./stopwords.txt') as stopwords_file:
    stopwords = [x.strip() for x in stopwords_file.readlines()]

stopwords[:10]

['و', 'در', 'به', 'از', 'که', 'این', 'را', 'با', 'است', 'برای']

And punctuations (English + Persian) ...

In [19]:
import string
punctuations = list(set('.:!،؛؟«»{}()<>[]' + string.punctuation))
punctuations

['"',
 '-',
 '؟',
 '<',
 '«',
 '@',
 '*',
 '؛',
 '+',
 ':',
 "'",
 ';',
 '^',
 '.',
 '$',
 '`',
 '[',
 ',',
 '{',
 '%',
 ')',
 '،',
 '&',
 '\\',
 '|',
 '!',
 ']',
 '»',
 '(',
 '_',
 '~',
 '=',
 '>',
 '#',
 '/',
 '?',
 '}']

And then remove punctuation and stopwords.

In [20]:
remove_words = punctuations + stopwords
words_cleaned = [t for t in tqdm.tqdm(words_flat) if t not in remove_words]

100%|██████████| 531775/531775 [00:02<00:00, 216426.42it/s]


And count again:

In [21]:
print('Number of words (excluding punctutaions and stopword): ', len(words_cleaned))
print ('Number of unique words: ', len(set(words_cleaned)))
average = np.sum([len(word) for word in words_cleaned])/len(words_cleaned)
print ('Average word length', average)
print ('Longest word', words_cleaned[np.argmax([len(word) for word in words_cleaned])])

Number of words (excluding punctutaions and stopword):  259101
Number of unique words:  28097
Average word length 5.321345730043497
Longest word Monster Hunter Stories ۲: Wings of Ruin


Now I count common words again, with their percentage in all words. As expected, words like 'بازی', 'فیلم' ... and console names like play station an Xbox are in most common words (If we didn't consider different writings this result would change, and Xbox count would decrease a lot). I didn't remove english stop words but I could (It wasn't very important)

In [22]:
common_words_cleaned = FreqDist(words_cleaned).most_common(50)
common_words_df = pd.DataFrame(common_words_cleaned, columns=['word','count'])
common_words_df['percent'] = common_words_df['count']/len(words_cleaned) * 100
common_words_df

word  count   percent
0         بازی   5742  2.216124
1         فیلم   4110  1.586254
2          سال   1608  0.620607
3         قرار   1598  0.616748
4        خواهد   1506  0.581241
5        سریال   1505  0.580855
6        عنوان   1205  0.465070
7        آن‌ها   1200  0.463140
8     بازی‌های   1111  0.428790
9        منتشر    977  0.377073
10           ش    889  0.343109
11         نقش    846  0.326514
12  پلی-استیشن    828  0.319567
13         نام    825  0.318409
14         The    809  0.312233
15      داستان    771  0.297567
16          of    740  0.285603
17         دست    735  0.283673
18        شرکت    725  0.279814
19     استفاده    722  0.278656
20       تاریخ    634  0.244692
21       شخصیت    634  0.244692
22         کار    618  0.238517
23   ایکس-باکس    611  0.235815
24       دنیای    595  0.229640
25        زمان    594  0.229254
26        ساخت    582  0.224623
27         سری    577  0.222693
28        فروش    547  0.211115
29        اصلی    542  0.209185
30        توسط    541  0.208799
31        صورت    541  0.208799
32        عرضه    539  0.208027
33       سرویس    537  0.207255
34           ۵    536  0.206869
35       اعلام    527  0.203396
36        حضور    513  0.197992
37   می‌توانید    505  0.194905
38      میلادی    480  0.185256
39           ۲    474  0.182940
40         فصل    474  0.182940
41       ادامه    471  0.181782
42    استودیوی    463  0.178695
43         ماه    461  0.177923
44       معرفی    459  0.177151
45      انتشار    439  0.169432
46        شاهد    434  0.167502
47        توجه    432  0.166730
48       کنسول    429  0.165572
49      نسخه‌ی    427  0.164801

## Important Games

Now I filter words that are a game name

In [23]:
game_tokens = list(filter(lambda word: word in games_normalized, words_cleaned))
game_tokens[:20]

['Bugsnax',
 'For Honor',
 'Gran Turismo ۷',
 'Horizon Forbidden West',
 'Gran Turismo ۷',
 'Horizon Forbidden West',
 'Ghost of Tsushima',
 'Kirby and the Forgotten Land',
 'Elden Ring',
 'WWE ۲K۲۲',
 'Elden Ring',
 'Elden Ring',
 'Elden Ring',
 'Elden Ring',
 'Elden Ring',
 'Gran Turismo ۷',
 'Halo Infinite',
 'Halo Infinite',
 'Halo Infinite',
 'Halo Infinite']

And find the most important games. Note that If I have not merged game tokens, I couldn't count the occurance of each game, so I had to retokenize all game names and make them Named Entities.

In [24]:
common_games = FreqDist(game_tokens).most_common(50)
common_games_df = pd.DataFrame(common_games, columns=['game','count'])
common_games_df

game  count
0                           Elden Ring    236
1                       Gran Turismo ۷     70
2                       Cyberpunk ۲۰۷۷     48
3                        Halo Infinite     43
4                         Apex Legends     26
5               Horizon Forbidden West     22
6                        Dying Light ۲     21
7                      Death Stranding     18
8                            Far Cry ۶     18
9                     Shadow Warrior ۳     16
10                   Ghost of Tsushima     15
11                             FIFA ۲۲     13
12                           Fallout ۴     13
13                          Dark Souls     12
14                     Forza Horizon ۵     12
15                           Firewatch     10
16                         Inscryption      9
17                           Destiny ۲      9
18        Kirby and the Forgotten Land      8
19                            WWE ۲K۲۲      7
20                            Among Us      7
21                           Far Cry ۴      7
22                           Far Cry ۵      7
23                         Dying Light      7
24                              NHL ۲۲      7
25                          Dead Cells      6
26              Immortals Fenyx Rising      6
27                       Metroid Dread      6
28                    Ghostwire: Tokyo      6
29                         Hyper Scape      6
30              Call of Duty: Vanguard      6
31                           Days Gone      5
32             Dragon Age: Inquisition      5
33                       Borderlands ۳      5
34                  Dynasty Warriors ۹      5
35                       Knockout City      5
36                             Bugsnax      4
37                   Enter the Gungeon      4
38                           Deathloop      4
39                          Fallout ۷۶      4
40                         Dead Island      4
41                          Dishonored      4
42  Lego Star Wars: The Skywalker Saga      4
43                        Back ۴ Blood      4
44                              Flappy      4
45                        Chrono Cross      3
46                        Doom Eternal      3
47                              Flicky      3
48                             Gears ۵      3
49                            BioShock      3